In [4]:
#pip install numpy

Note: you may need to restart the kernel to use updated packages.


In [2]:
#pip install -U ydata-profiling

     |████████████████████████████████| 357 kB 1.0 MB/s eta 0:00:01
     |████████████████████████████████| 172 kB 29.9 MB/s eta 0:00:01
     |████████████████████████████████| 296 kB 17.3 MB/s eta 0:00:01
     |████████████████████████████████| 102 kB 24.1 MB/s eta 0:00:01
     |████████████████████████████████| 381 kB 27.4 MB/s eta 0:00:01
     |████████████████████████████████| 10.5 MB 242 kB/s eta 0:00:01
     |████████████████████████████████| 2.6 MB 27.5 MB/s eta 0:00:01
     |████████████████████████████████| 31.0 MB 1.1 MB/s eta 0:00:011
     |████████████████████████████████| 1.9 MB 11.9 MB/s eta 0:00:01
     |████████████████████████████████| 17.6 MB 6.6 MB/s eta 0:00:01
     |████████████████████████████████| 53 kB 8.4 MB/s  eta 0:00:01
     |████████████████████████████████| 233 kB 13.9 MB/s eta 0:00:01
  Attempting uninstall: numpy
    Found existing installation: numpy 1.24.3
    Uninstalling numpy-1.24.3:
      Successfully uninstalled numpy-1.24.3
  Attempting uninstall

  Attempting uninstall: patsy
    Found existing installation: patsy 0.5.1
    Uninstalling patsy-0.5.1:
      Successfully uninstalled patsy-0.5.1
  Attempting uninstall: packaging
    Found existing installation: packaging 20.9
    Uninstalling packaging-20.9:
      Successfully uninstalled packaging-20.9
  Attempting uninstall: llvmlite
    Found existing installation: llvmlite 0.36.0
    Uninstalling llvmlite-0.36.0:
      Successfully uninstalled llvmlite-0.36.0
  Attempting uninstall: imagehash
    Found existing installation: ImageHash 4.2.1
    Uninstalling ImageHash-4.2.1:
      Successfully uninstalled ImageHash-4.2.1
  Attempting uninstall: statsmodels
    Found existing installation: statsmodels 0.12.2
    Uninstalling statsmodels-0.12.2:
      Successfully uninstalled statsmodels-0.12.2
  Attempting uninstall: pydantic
    Found existing installation: pydantic 1.9.0
    Uninstalling pydantic-1.9.0:
      Successfully uninstalled pydantic-1.9.0
  Attempting uninstall: numba

In [1]:
import pandas as pd
import json
import os
from collections import Counter
import numpy as np
from ydata_profiling import ProfileReport

In [2]:
pwd

'/Users/majurocu/Desktop/OneDrive_1_28-01-2024'

In [3]:
data_dir = '/Users/majurocu/Desktop/OneDrive_1_28-01-2024'

### Functions

In [4]:
cd extracted/

/Users/majurocu/Desktop/OneDrive_1_28-01-2024/extracted


In [5]:
def json_files_to_df():
    json_files = [f for f in os.listdir() if f.endswith('.json')]
    
    for json_file in json_files:
        df = one_json_to_df(json_file)
        dfs.append(df)

In [6]:
def one_json_to_df (file):
    json_file = open(file)
    json_dicc = json.load(json_file)
    df_generalDesc = pd.json_normalize(json_dicc['generalDesc'])
    df_contributionDesc_authors = pd.json_normalize(json_dicc ['contributionDesc']['authors'])
    df_curators = pd.json_normalize(json_dicc ['contributionDesc']['curators'])
    df_institutions = pd.json_normalize(json_dicc ['contributionDesc']['institutions'])
    df_fundings = pd.json_normalize(json_dicc ['contributionDesc']['fundings'])
    df_experimentalDetails = pd.json_normalize(json_dicc ['experimentalDetails'])
    df_characteristics = pd.json_normalize(json_dicc ['characteristic'])
    df_bioDescrip = pd.json_normalize(json_dicc ['bioDescription'])
    df_summary = pd.json_normalize(json_dicc ['bioSummary'])
    df_provenance = pd.json_normalize(json_dicc ['provenance'])
            
    df_institutions = df_institutions.rename(columns={'name':'institution_name','longName':'logName'})
            
    working_df = pd.concat([df_generalDesc, df_contributionDesc_authors, df_curators,
                            df_institutions, df_fundings, df_experimentalDetails, df_characteristics,
                            df_bioDescrip, df_summary, df_provenance], axis=1)
            
    working_df['species'] = json_dicc ['species']
    working_df['dataCategory'] = json_dicc ['dataCategory']
    working_df['id_experiment'] = json_dicc ['id']

    return working_df

### Functions for one data frame

In [7]:
# For one data frame
def count_words(phrase):
    words = phrase.split()
    return len(words)

In [8]:
# For one data frame
def character_long (new_list, row_header, number_of_elements,df):
    for value in number_of_elements:
        valor = len(df[row_header][value])
        new_list.append(valor)
    return new_list

In [9]:
#For one data frame
def number_of_words (row_header, number_of_elements, df,lista):
    for value in number_of_elements:
        phrase = df[row_header][value]
        words_test = count_words(phrase)
        lista.append(words_test)
    return lista

In [10]:
#For one data frame
def missing_values_table(df): 
        mis_val = df.isnull().sum()
        mis_val_percent = 100 * df.isnull().sum()/len(df)
        mis_val_table = pd.concat([mis_val, mis_val_percent], axis=1)
        mis_val_table_ren_columns = mis_val_table.rename(
        columns = {0 : 'Missing Values', 1 : '% of Total Values'})
        return mis_val_table_ren_columns 

In [11]:
#For one data frame
def entities_recognition(feature,df):
    lista = []
    count = 0
    while count < len(df):
        phrase = df[feature][count]
        doc_phrase = nlp(phrase)
        value_to_list = list(doc_phrase.ents)
        lista.append(value_to_list)
        count += 1
        
    return lista

In [12]:
#For one data frame
def lista_entities_to_strings(lista):
    count = 0
    lista_all_strings = []
    while count < len(lista):
        list_of_string = [span.text for span in lista[count]]
        lista_all_strings.append(list_of_string)
        count +=1

    return lista_all_strings

In [13]:
#For one data frame
def count_entities (feature,df):
    count = 0
    lista_amount = []
    while count < len(df):
        value = len(df[feature][count])
        lista_amount.append(value)
        count += 1
        
    return lista_amount

## Analysing all json files

### Open all files

In [6]:
cd extracted/

/Users/s2531396/Library/CloudStorage/OneDrive-UniversityofEdinburgh/PhD/Code/extracted


In [14]:
json_files = [f for f in os.listdir() if f.endswith('.json')]
json_files

['13232.json',
 '16030.json',
 '13662.json',
 '12970.json',
 '16460.json',
 '13398.json',
 '12423.json',
 '16933.json',
 '12073.json',
 '16899.json',
 '15759.json',
 '16876.json',
 '12566.json',
 '15309.json',
 '12136.json',
 '16175.json',
 '14148.json',
 '13377.json',
 '16525.json',
 '14518.json',
 '13727.json',
 '12835.json',
 '15020.json',
 '15470.json',
 '11960.json',
 '10672.json',
 '15923.json',
 '14631.json',
 '11433.json',
 '11599.json',
 '14261.json',
 '15889.json',
 '11063.json',
 '15866.json',
 '14774.json',
 '16749.json',
 '11126.json',
 '14324.json',
 '16319.json',
 '17158.json',
 '15165.json',
 '11825.json',
 '13818.json',
 '15535.json',
 '17226.json',
 '12024.json',
 '16964.json',
 '14959.json',
 '12474.json',
 '13635.json',
 '11608.json',
 '12927.json',
 '16067.json',
 '11258.json',
 '13770.json',
 '16088.json',
 '12862.json',
 '16572.json',
 '13320.json',
 '16122.json',
 '12161.json',
 '12531.json',
 '16821.json',
 '11034.json',
 '13009.json',
 '14236.json',
 '13390707

In [15]:
dfs =[]

In [16]:
for json_file in json_files:
    df = one_json_to_df(json_file)
    dfs.append(df)

In [17]:
for i, df in enumerate(dfs):
    print(f"DataFrame {i+1}:")
    print(df)
    print('\n'+'-'*40 + '\n')

DataFrame 1:
                        name  \
0  10012018 gst3-luc in ppp1   

                                             purpose  \
0  first time to run gst3-luc in wt and cross pro...   

                 description comments    id     login firstName lastName  \
0  result is really weird...     None  1324  dzhaolan   Zhaolan     Ding   

  ORCID institution_name  ... materialTypes materialOrigins customTags  \
0  None             TAMU  ...            []              []         []   

  externalIds                              created     createdBy  \
0          []  [2018, 10, 2, 2, 57, 55, 178000000]  Zhaolan Ding   

                            modified    modifiedBy   dataCategory  \
0  [2018, 10, 2, 3, 1, 9, 265000000]  Zhaolan Ding  EXPR_REPORTER   

   id_experiment  
0          13232  

[1 rows x 46 columns]

----------------------------------------

DataFrame 2:
                                                name  \
0  CCD2 2020Ene31 xc2307 LNNccd: Entrenamiento 22...   

 

[1 rows x 46 columns]

----------------------------------------

DataFrame 47:
                                                name  \
0  LUMO DF DD Wyalkatchem 1 cm ROIs adjusted to l...   

                                             purpose description comments  \
0  Intial optimisation of LUMO camera for DF meas...        None     None   

   executionDate    id         login firstName lastName ORCID  ...  \
0  [2020, 6, 29]  2415  chrisbuckley     Chris  Buckley  None  ...   

  materialTypes materialOrigins customTags externalIds  \
0            []              []         []          []   

                               created      createdBy  \
0  [2020, 7, 13, 13, 56, 3, 862317000]  Chris Buckley   

                              modified     modifiedBy          dataCategory  \
0  [2020, 7, 14, 0, 55, 13, 769255000]  Chris Buckley  DELAYED_FLUORESCENCE   

   id_experiment  
0          16964  

[1 rows x 48 columns]

----------------------------------------

DataFrame 48:
   

[1 rows x 46 columns]

----------------------------------------

DataFrame 87:
                      name                                            purpose  \
0  Topcount data from York  Checking import problems with their topcount d...   

  description comments    id login firstName lastName ORCID  \
0        None     None  1003  test      Test     User  None   

          institution_name  ... materialTypes materialOrigins customTags  \
0  University of Edinburgh  ...            []              []         []   

  externalIds                                created  createdBy  \
0          []  [2017, 11, 21, 13, 21, 33, 668000000]  Test User   

                               modified modifiedBy   dataCategory  \
0  [2018, 1, 17, 17, 38, 20, 955000000]  Test User  EXPR_REPORTER   

   id_experiment  
0          11521  

[1 rows x 46 columns]

----------------------------------------

DataFrame 88:
                                name  \
0  tracks_02Oct18_c_RLL_phyb_control   

     

[1 rows x 47 columns]

----------------------------------------

DataFrame 128:
                   name                                            purpose  \
0  kymographs_30Jan17_c  To test the period of the clock across longitu...   

  description comments    id           login firstName   lastName ORCID  \
0        None     None  1466  mark.greenwood      Mark  Greenwood  None   

          institution_name  ... materialTypes materialOrigins customTags  \
0  University of Cambridge  ...            []              []         []   

  externalIds                               created       createdBy  \
0          []  [2018, 2, 23, 14, 53, 13, 989000000]  Mark Greenwood   

                               modified      modifiedBy   dataCategory  \
0  [2018, 2, 23, 14, 54, 26, 286000000]  Mark Greenwood  EXPR_REPORTER   

   id_experiment  
0          12065  

[1 rows x 46 columns]

----------------------------------------

DataFrame 129:
                name                            

[1 rows x 46 columns]

----------------------------------------

DataFrame 172:
                                                name  \
0  The Effect of Mutations in Auxin Transport and...   
1                                                NaN   

                                             purpose  \
0  Testing whether mutations in auxin transporter...   
1                                                NaN   

                                         description  \
0  Arabidopis thaliana seeds with different auxin...   
1                                                NaN   

                                            comments      id   login  \
0  Visible fungal infection, but the plants looke...  1663.0  icarre   
1                                                NaN     NaN    None   

  firstName  lastName ORCID       institution_name  ... materialTypes  \
0  Isabelle     Carre  None  University of Warwick  ...            []   
1    Archie  Stephens  None                    NaN

...

DataFrame 5661:
                      name                                            purpose  \
0  Circadian Clock Nitrate  Nitrate impacts the oscillation of circadian c...   

  description comments    id   login  firstName lastName ORCID  \
0        None     None  1152  tp2017  Christian  Hermans  None   

  institution_name  ... materialTypes materialOrigins customTags externalIds  \
0              ULB  ...            []              []         []          []   

                             created          createdBy  \
0  [2017, 3, 8, 9, 10, 59, 74000000]  Christian Hermans   

                             modified         modifiedBy   dataCategory  \
0  [2017, 3, 8, 9, 31, 20, 834000000]  Christian Hermans  EXPR_REPORTER   

   id_experiment  
0          10630  

[1 rows x 43 columns]

----------------------------------------

DataFrame 5662:
                                name  \
0  kymographs_20Feb18_b_DD_temp_PRR9   

                                             purpose des

[1 rows x 43 columns]

----------------------------------------

DataFrame 5710:
       name                                            purpose description  \
0  Andor300  Andor300- see google sheet for experimental de...        None   

  comments    id    login firstName lastName ORCID     institution_name  ...  \
0     None  1142  majonea      Matt    Jones  None  University of Essex  ...   

  materialTypes materialOrigins customTags externalIds  \
0            []              []         []          []   

                               created   createdBy  \
0  [2019, 5, 29, 11, 55, 0, 177235000]  Matt Jones   

                               modified  modifiedBy   dataCategory  \
0  [2019, 5, 29, 11, 55, 58, 432063000]  Matt Jones  EXPR_REPORTER   

   id_experiment  
0          14599  

[1 rows x 46 columns]

----------------------------------------

DataFrame 5711:
               name                                            purpose  \
0  pCAB in LD 12:12  Here, we measured t

[1 rows x 46 columns]

----------------------------------------

DataFrame 5759:
               name                                            purpose  \
0  Abiotic stresses  How do abiotic stresses modulate the soybean c...   

                                         description comments    id  \
0  Plants were grown in soil for 14 days and give...     None  1252   

        login firstName lastName ORCID       institution_name  ...  \
0  oneway1985       Wei     Wang  None  Iowa State University  ...   

  materialTypes materialOrigins customTags externalIds  \
0            []              []         []          []   

                               created createdBy  \
0  [2017, 6, 15, 1, 49, 41, 819000000]  Wei Wang   

                             modified modifiedBy  dataCategory  id_experiment  
0  [2017, 6, 30, 2, 21, 45, 94000000]   Wei Wang    TRANSCRIPT          10831  

[1 rows x 43 columns]

----------------------------------------

DataFrame 5760:
                      

[1 rows x 47 columns]

----------------------------------------

DataFrame 5808:
                 name                                            purpose  \
0  LL3_DM10 WT vs mut  test if problem of period shortening in mutant...   

  description comments    id   login firstName lastName ORCID  \
0        None     None  1543  elisec     Elise      Cau  None   

         institution_name  ... materialTypes materialOrigins customTags  \
0  University of Toulouse  ...            []              []         []   

  externalIds                             created  createdBy  \
0          []  [2018, 11, 6, 8, 20, 5, 947000000]  Elise Cau   

                             modified modifiedBy  dataCategory  id_experiment  
0  [2018, 11, 6, 8, 53, 2, 553000000]  Elise Cau     BEHAVIOUR          13421  

[1 rows x 46 columns]

----------------------------------------

DataFrame 5809:
                          name  \
0  Cry1luc 1mM AlkK April 2020   

                                            

[1 rows x 46 columns]

----------------------------------------

DataFrame 5858:
                                       name  \
0  Tecan 3.19.2020 ccaluc 1306a7 phee401-a4   

                                             purpose  \
0  CRISPR goes green: CRISPR-Cas9 in plants\nA ge...   

                                         description comments    id     login  \
0  CRISPR goes green: CRISPR-Cas9 in plants\nA ge...     None  2097  tonglian   

  firstName lastName ORCID institution_name  ... materialTypes  \
0      Tong    Liang  None              USC  ...            []   

  materialOrigins customTags externalIds                              created  \
0              []         []          []  [2020, 3, 28, 3, 50, 20, 615547000]   

    createdBy                            modified  modifiedBy   dataCategory  \
0  Tong Liang  [2020, 3, 28, 3, 55, 9, 123412000]  Tong Liang  EXPR_REPORTER   

   id_experiment  
0          16361  

[1 rows x 47 columns]

-----------------------------

In [18]:
dfs[1]

name  \
0  CCD2 2020Ene31 xc2307 LNNccd: Entrenamiento 22...   

                                             purpose description comments  \
0  Obtener oscilaciones luego de un entrenamiento...                 None   

   executionDate    id    login firstName lastName ORCID  ... materialTypes  \
0  [2020, 2, 21]  1748  vdelrio  Verónica  Del Rio  None  ...            []   

  materialOrigins customTags externalIds  \
0              []         []          []   

                                created         createdBy  \
0  [2020, 2, 21, 16, 42, 14, 390192000]  Verónica Del Rio   

                               modified        modifiedBy   dataCategory  \
0  [2020, 2, 21, 22, 19, 33, 436789000]  Verónica Del Rio  EXPR_REPORTER   

   id_experiment  
0          16030  

[1 rows x 48 columns]

### Number of words

In [94]:
def number_of_words (row_header, number_of_elements, df,lista):
    count = 0
    for value in number_of_elements:
        
        if count < len(df):
            objeto = df[value][row_header]
            complete_phrase = objeto.to_string()
            phrase = complete_phrase.split()
            phrase.pop(0)
            total_number = len(phrase)
            lista.append(total_number)
            count +=1
        else:
            break
    return lista

In [19]:
len(dfs)

5858

In [20]:
def createList(r1, r2):
    return list(range(r1, r2+1))

In [60]:
all_elements = createList(0,len(dfs))
type(all_elements)

list

#### Purpouse

In [124]:
new_list_4 = []
row_header = "purpose"
purpose_number_words = number_of_words(row_header,all_elements,dfs,new_list_4)
purpose_number_words

[10,
 6,
 9,
 9,
 9,
 8,
 7,
 6,
 9,
 7,
 11,
 8,
 8,
 8,
 7,
 6,
 11,
 6,
 9,
 8,
 7,
 8,
 7,
 7,
 7,
 11,
 8,
 10,
 11,
 6,
 9,
 7,
 10,
 8,
 8,
 9,
 9,
 7,
 9,
 6,
 5,
 8,
 9,
 8,
 7,
 7,
 8,
 8,
 9,
 8,
 6,
 10,
 7,
 8,
 8,
 7,
 8,
 8,
 9,
 7,
 8,
 10,
 7,
 8,
 10,
 10,
 4,
 6,
 8,
 7,
 8,
 10,
 7,
 9,
 7,
 7,
 9,
 10,
 9,
 9,
 6,
 6,
 7,
 9,
 8,
 7,
 7,
 8,
 8,
 8,
 9,
 9,
 10,
 11,
 8,
 9,
 7,
 9,
 11,
 6,
 8,
 8,
 8,
 9,
 9,
 7,
 9,
 8,
 8,
 8,
 9,
 6,
 9,
 8,
 7,
 8,
 8,
 7,
 9,
 7,
 8,
 9,
 6,
 7,
 8,
 5,
 7,
 9,
 8,
 6,
 7,
 8,
 8,
 10,
 8,
 8,
 11,
 10,
 8,
 8,
 7,
 10,
 9,
 9,
 7,
 9,
 10,
 8,
 9,
 6,
 7,
 6,
 9,
 11,
 7,
 7,
 8,
 11,
 7,
 7,
 7,
 6,
 7,
 9,
 7,
 9,
 9,
 7,
 6,
 8,
 9,
 8,
 7,
 8,
 7,
 9,
 8,
 8,
 7,
 9,
 8,
 5,
 9,
 4,
 6,
 9,
 8,
 10,
 8,
 6,
 10,
 9,
 8,
 9,
 10,
 8,
 7,
 7,
 10,
 8,
 8,
 14,
 9,
 9,
 9,
 8,
 7,
 6,
 8,
 8,
 10,
 7,
 9,
 8,
 11,
 11,
 11,
 8,
 5,
 12,
 9,
 7,
 8,
 8,
 6,
 8,
 7,
 8,
 9,
 6,
 9,
 8,
 9,
 8,
 8,
 6,
 10,
 7,
 8,
 8,
 6,
 9

In [148]:
count = 0
while count < len(dfs):
    dfs[count]["number_of_words_purpose"] = purpose_number_words[count]
    count += 1

In [150]:
dfs[50]

name  \
0  Retina Temperature Compensation   

                                             purpose description comments  \
0  Testing Retina Temperature Compensation: P2L f...        None     None   

     id    login firstName lastName ORCID  \
0  1272  apatton    Andrew   Patton  None   

                      institution_name  ... materialOrigins customTags  \
0  MRC Laboratory of Molecular Biology  ...              []         []   

  externalIds                               created      createdBy  \
0          []  [2017, 12, 6, 16, 39, 34, 107000000]  Andrew Patton   

                              modified     modifiedBy   dataCategory  \
0  [2017, 12, 6, 16, 57, 42, 21000000]  Andrew Patton  EXPR_REPORTER   

   id_experiment  number_of_words_purpose  
0          11608                        6  

[1 rows x 44 columns]

#### Name

In [152]:
new_list_5 = []
row_header = "name"
name_number_words = number_of_words(row_header,all_elements,dfs,new_list_5)
name_number_words

[4,
 6,
 5,
 1,
 3,
 3,
 6,
 8,
 1,
 1,
 4,
 1,
 8,
 1,
 6,
 6,
 4,
 2,
 9,
 1,
 1,
 1,
 8,
 1,
 8,
 2,
 4,
 5,
 5,
 1,
 4,
 4,
 9,
 3,
 5,
 1,
 1,
 3,
 2,
 5,
 2,
 6,
 3,
 4,
 5,
 1,
 10,
 1,
 9,
 3,
 3,
 1,
 6,
 5,
 1,
 2,
 3,
 2,
 7,
 1,
 4,
 7,
 2,
 4,
 8,
 3,
 5,
 2,
 3,
 6,
 4,
 7,
 1,
 2,
 2,
 5,
 4,
 2,
 3,
 2,
 6,
 4,
 6,
 1,
 7,
 1,
 4,
 1,
 6,
 1,
 4,
 1,
 5,
 9,
 1,
 1,
 5,
 5,
 3,
 5,
 5,
 9,
 6,
 4,
 7,
 1,
 1,
 7,
 1,
 1,
 2,
 1,
 4,
 8,
 6,
 7,
 5,
 2,
 2,
 3,
 1,
 7,
 8,
 2,
 1,
 3,
 4,
 1,
 3,
 1,
 5,
 2,
 5,
 7,
 5,
 7,
 3,
 1,
 2,
 3,
 1,
 7,
 1,
 3,
 1,
 4,
 1,
 3,
 2,
 6,
 5,
 5,
 6,
 4,
 8,
 1,
 6,
 2,
 7,
 3,
 6,
 5,
 1,
 3,
 5,
 1,
 7,
 4,
 6,
 7,
 5,
 10,
 3,
 7,
 1,
 5,
 2,
 1,
 1,
 3,
 1,
 1,
 1,
 5,
 5,
 2,
 3,
 5,
 4,
 1,
 1,
 3,
 1,
 1,
 8,
 3,
 4,
 4,
 3,
 8,
 2,
 1,
 3,
 4,
 5,
 1,
 2,
 3,
 4,
 3,
 2,
 7,
 7,
 1,
 9,
 9,
 1,
 2,
 5,
 2,
 5,
 4,
 5,
 3,
 3,
 1,
 1,
 6,
 1,
 1,
 7,
 4,
 2,
 8,
 3,
 7,
 2,
 7,
 4,
 1,
 9,
 5,
 5,
 4,
 1,
 7,
 3,
 1,
 6,
 8

In [153]:
count = 0
while count < len(dfs):
    dfs[count]["number_of_words_name"] = name_number_words[count]
    count += 1

In [154]:
dfs[50]

name  \
0  Retina Temperature Compensation   

                                             purpose description comments  \
0  Testing Retina Temperature Compensation: P2L f...        None     None   

     id    login firstName lastName ORCID  \
0  1272  apatton    Andrew   Patton  None   

                      institution_name  ... customTags externalIds  \
0  MRC Laboratory of Molecular Biology  ...         []          []   

                                created      createdBy  \
0  [2017, 12, 6, 16, 39, 34, 107000000]  Andrew Patton   

                              modified     modifiedBy   dataCategory  \
0  [2017, 12, 6, 16, 57, 42, 21000000]  Andrew Patton  EXPR_REPORTER   

  id_experiment  number_of_words_purpose  number_of_words_name  
0         11608                        6                     3  

[1 rows x 45 columns]

#### Description

In [159]:
new_list_7 = []
row_header = "description"
description_number_words = number_of_words(row_header,all_elements,dfs,new_list_7)
description_number_words

[4,
 0,
 1,
 6,
 1,
 1,
 7,
 4,
 1,
 8,
 1,
 1,
 1,
 1,
 1,
 8,
 1,
 5,
 8,
 1,
 1,
 1,
 7,
 1,
 7,
 1,
 1,
 1,
 1,
 1,
 11,
 1,
 9,
 8,
 10,
 1,
 1,
 1,
 5,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 6,
 1,
 1,
 1,
 5,
 7,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 10,
 1,
 10,
 1,
 1,
 6,
 8,
 8,
 8,
 8,
 1,
 1,
 6,
 7,
 1,
 11,
 10,
 7,
 7,
 6,
 6,
 8,
 1,
 1,
 7,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 5,
 1,
 1,
 1,
 1,
 11,
 6,
 1,
 9,
 8,
 9,
 1,
 1,
 1,
 9,
 1,
 1,
 1,
 1,
 8,
 8,
 8,
 9,
 9,
 1,
 1,
 8,
 1,
 1,
 6,
 1,
 1,
 6,
 1,
 1,
 7,
 1,
 1,
 1,
 1,
 1,
 1,
 9,
 1,
 9,
 1,
 9,
 7,
 1,
 1,
 1,
 1,
 7,
 10,
 1,
 1,
 6,
 1,
 9,
 1,
 10,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 6,
 1,
 1,
 8,
 1,
 7,
 1,
 6,
 8,
 1,
 8,
 1,
 9,
 2,
 1,
 1,
 1,
 1,
 9,
 1,
 1,
 1,
 7,
 8,
 1,
 5,
 1,
 1,
 6,
 1,
 1,
 1,
 1,
 11,
 9,
 8,
 6,
 1,
 8,
 6,
 12,
 1,
 9,
 1,
 1,
 5,
 6,
 1,
 1,
 1,
 4,
 10,
 8,
 8,
 1,
 1,
 7,
 1,
 1,
 1,
 7,
 1,
 1,
 1,
 8,
 7,
 1,
 1,
 7,
 9,
 6,
 1,
 8,
 1,
 12,
 1,
 1,
 1,
 1,
 3,
 9,
 1,
 1,
 1,
 1,
 1,

In [160]:
count = 0
while count < len(dfs):
    dfs[count]["number_of_words_description"] = description_number_words[count]
    count += 1

In [166]:
dfs[2]

name  \
0  MINT-Fly data day-by-day Weeks 1-2   

                                             purpose description comments  \
0  Observing the change in phase of activity of f...        None     None   

     id               login   firstName  lastName ORCID  \
0  1793  panayiotissoteriou  Panayiotis  Soteriou  None   

                         institution_name  ... externalIds  \
0  Ludwig-Maximilians-Universität München  ...          []   

                               created            createdBy  \
0  [2018, 12, 6, 17, 44, 4, 519000000]  Panayiotis Soteriou   

                               modified           modifiedBy dataCategory  \
0  [2018, 12, 6, 17, 47, 39, 891000000]  Panayiotis Soteriou    BEHAVIOUR   

  id_experiment number_of_words_purpose  number_of_words_name  \
0         13662                       9                     5   

   number_of_words_description  
0                            1  

[1 rows x 49 columns]

#### Comments

In [165]:
new_list_9 = []
row_header = "comments"
comments_number_words = number_of_words(row_header,all_elements,dfs,new_list_9)
comments_number_words

[1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 5,
 5,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 10,
 1,
 1,
 1,
 1,
 7,
 2,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 10,
 1,
 1,
 6,
 6,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 8,
 1,
 1,
 1,
 1,
 11,
 1,
 1,
 8,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 2,
 5,
 1,
 1,
 1,
 1,
 1,
 6,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 5,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 6,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 6,
 1,
 1,
 9,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 9,
 1,
 1,
 1,
 1,
 1,
 1,
 10,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 8,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 8,
 8,
 1,
 1,
 1,
 1,
 1,
 1,
 6,
 1,
 1,
 1,
 8,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 8,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,


In [167]:
count = 0
while count < len(dfs):
    dfs[count]["number_of_words_comments"] = comments_number_words[count]
    count += 1

In [195]:
dfs[1]

name  \
0  CCD2 2020Ene31 xc2307 LNNccd: Entrenamiento 22...   

                                             purpose description comments  \
0  Obtener oscilaciones luego de un entrenamiento...                 None   

   executionDate    id    login firstName lastName  \
0  [2020, 2, 21]  1748  vdelrio  Verónica  Del Rio   

                           institution_name  ...            species  \
0  Pontificia Universidad Católica de Chile  ...  Neurospora crassa   

                                created                              modified  \
0  [2020, 2, 21, 16, 42, 14, 390192000]  [2020, 2, 21, 22, 19, 33, 436789000]   

         modifiedBy   dataCategory id_experiment  number_of_words_purpose  \
0  Verónica Del Rio  EXPR_REPORTER         16030                        6   

   number_of_words_name  number_of_words_description  number_of_words_comments  
0                     6                            0                         1  

[1 rows x 35 columns]

### Number of characters

In [221]:
def character_long (row_header, number_of_elements, df, new_list):
    count = 0
    for value in number_of_elements:
        if count < len(df):
            valor = len(df[value][row_header][0])
            new_list.append(valor)
            count +=1
        else:
            break
    return new_list

In [222]:
len(dfs[0]["purpose"][0])

75

#### Name

In [224]:
new_list_12 = []
row_header = "name"
name_number_characters = character_long(row_header,all_elements,dfs,new_list_12)
name_number_characters

[25,
 59,
 34,
 7,
 17,
 19,
 45,
 58,
 20,
 10,
 27,
 19,
 51,
 7,
 61,
 91,
 29,
 18,
 50,
 28,
 8,
 30,
 65,
 10,
 67,
 8,
 29,
 23,
 26,
 16,
 29,
 23,
 50,
 16,
 34,
 11,
 10,
 12,
 10,
 39,
 9,
 27,
 17,
 34,
 55,
 20,
 55,
 31,
 52,
 13,
 31,
 27,
 46,
 31,
 24,
 17,
 27,
 8,
 47,
 19,
 19,
 35,
 16,
 19,
 58,
 14,
 30,
 6,
 21,
 43,
 26,
 30,
 7,
 11,
 21,
 19,
 29,
 12,
 12,
 16,
 100,
 24,
 43,
 13,
 55,
 12,
 23,
 33,
 43,
 21,
 26,
 26,
 27,
 50,
 16,
 16,
 29,
 27,
 12,
 23,
 22,
 50,
 35,
 35,
 47,
 15,
 9,
 27,
 24,
 22,
 11,
 18,
 42,
 60,
 44,
 36,
 33,
 10,
 13,
 37,
 36,
 64,
 55,
 10,
 13,
 29,
 24,
 20,
 17,
 6,
 19,
 8,
 38,
 26,
 21,
 27,
 25,
 19,
 8,
 17,
 9,
 71,
 18,
 16,
 25,
 23,
 23,
 18,
 20,
 54,
 37,
 22,
 34,
 18,
 34,
 25,
 33,
 16,
 28,
 14,
 33,
 28,
 23,
 9,
 39,
 15,
 34,
 28,
 50,
 48,
 30,
 75,
 16,
 33,
 22,
 25,
 15,
 8,
 7,
 18,
 35,
 10,
 11,
 42,
 23,
 16,
 14,
 25,
 28,
 8,
 21,
 28,
 8,
 24,
 51,
 16,
 24,
 34,
 24,
 100,
 17,
 9,
 11,
 1

In [225]:
count = 0
while count < len(dfs):
    dfs[count]["number_of_characters_names"] = name_number_characters[count]
    count += 1

#### Purpose

In [227]:
new_list_13 = []
row_header = "purpose"
purpose_number_characters = character_long(row_header,all_elements,dfs,new_list_13)
purpose_number_characters

[75,
 62,
 63,
 94,
 87,
 65,
 103,
 76,
 79,
 75,
 88,
 68,
 69,
 89,
 55,
 114,
 61,
 56,
 83,
 84,
 58,
 97,
 166,
 78,
 125,
 72,
 71,
 67,
 57,
 64,
 94,
 87,
 95,
 129,
 127,
 120,
 70,
 63,
 63,
 99,
 110,
 69,
 103,
 78,
 70,
 78,
 75,
 69,
 84,
 65,
 83,
 69,
 74,
 72,
 61,
 89,
 101,
 64,
 91,
 71,
 81,
 73,
 59,
 64,
 145,
 60,
 38,
 57,
 58,
 227,
 57,
 70,
 78,
 67,
 83,
 72,
 56,
 83,
 79,
 74,
 1239,
 60,
 227,
 75,
 93,
 75,
 61,
 80,
 75,
 80,
 77,
 62,
 81,
 353,
 73,
 78,
 70,
 77,
 55,
 63,
 63,
 90,
 64,
 168,
 93,
 600,
 56,
 75,
 62,
 66,
 67,
 66,
 75,
 59,
 227,
 67,
 90,
 60,
 56,
 96,
 101,
 76,
 278,
 66,
 93,
 67,
 205,
 82,
 59,
 80,
 56,
 61,
 63,
 70,
 68,
 75,
 69,
 227,
 59,
 156,
 59,
 96,
 65,
 66,
 80,
 70,
 66,
 89,
 64,
 60,
 83,
 110,
 65,
 65,
 57,
 60,
 60,
 70,
 72,
 72,
 68,
 87,
 78,
 70,
 58,
 71,
 77,
 205,
 59,
 74,
 65,
 145,
 98,
 80,
 144,
 63,
 66,
 112,
 59,
 97,
 82,
 55,
 132,
 130,
 83,
 84,
 67,
 57,
 67,
 59,
 62,
 68,
 567,
 59

In [228]:
count = 0
while count < len(dfs):
    dfs[count]["number_of_characters_purpose"] = purpose_number_characters[count]
    count += 1

#### Description

In [231]:
new_list_14 = []
row_header = "description"
description_number_characters = character_long(row_header,all_elements,dfs,new_list_14)
description_number_characters

TypeError: object of type 'NoneType' has no len()

In [ ]:
count = 0
while count < len(dfs):
    dfs[count]["number_of_characters_description"] = description_number_characters[count]
    count += 1

#### Comments

In [232]:
new_list_15 = []
row_header = "comments"
comments_number_characters = character_long(row_header,all_elements,dfs,new_list_15)
comments_number_characters

TypeError: object of type 'NoneType' has no len()

In [ ]:
count = 0
while count < len(dfs):
    dfs[count]["number_of_characters_comments"] = comments_number_characters[count]
    count += 1

### Editing Data frame

##### Removing columns

In [175]:
def column_to_remove(list_of_df, column_to_remove):
    for i, df in enumerate(dfs):
        if column_to_remove in df.columns:
            dfs[i] = df.drop(columns = column_to_remove)
        else:
            print(f"Data frame {i+1} does not have the column:'{column_to_remove}'.")

In [181]:
list_columns_to_remove = ["ORCID", "growthEnvironments.environments", "experimentalEnvironments.environments",
                         "licence", "bios", "labels", "ecotypes", "genotypes", "markers", "lines", 
                          "growthStages", "tagTypes", "materialTypes", "materialOrigins", "customTags",
                         "externalIds", "createdBy"]

In [182]:
for title in list_columns_to_remove:
    column_to_remove(dfs,title)
    print(title)

Data frame 1 does not have the column:'grownEnvironments.environments'.
Data frame 2 does not have the column:'grownEnvironments.environments'.
Data frame 3 does not have the column:'grownEnvironments.environments'.
Data frame 4 does not have the column:'grownEnvironments.environments'.
Data frame 5 does not have the column:'grownEnvironments.environments'.
Data frame 6 does not have the column:'grownEnvironments.environments'.
Data frame 7 does not have the column:'grownEnvironments.environments'.
Data frame 8 does not have the column:'grownEnvironments.environments'.
Data frame 9 does not have the column:'grownEnvironments.environments'.
Data frame 10 does not have the column:'grownEnvironments.environments'.
Data frame 11 does not have the column:'grownEnvironments.environments'.
Data frame 12 does not have the column:'grownEnvironments.environments'.
Data frame 13 does not have the column:'grownEnvironments.environments'.
Data frame 14 does not have the column:'grownEnvironments.en

Data frame 1925 does not have the column:'grownEnvironments.environments'.
Data frame 1926 does not have the column:'grownEnvironments.environments'.
Data frame 1927 does not have the column:'grownEnvironments.environments'.
Data frame 1928 does not have the column:'grownEnvironments.environments'.
Data frame 1929 does not have the column:'grownEnvironments.environments'.
Data frame 1930 does not have the column:'grownEnvironments.environments'.
Data frame 1931 does not have the column:'grownEnvironments.environments'.
Data frame 1932 does not have the column:'grownEnvironments.environments'.
Data frame 1933 does not have the column:'grownEnvironments.environments'.
Data frame 1934 does not have the column:'grownEnvironments.environments'.
Data frame 1935 does not have the column:'grownEnvironments.environments'.
Data frame 1936 does not have the column:'grownEnvironments.environments'.
Data frame 1937 does not have the column:'grownEnvironments.environments'.
Data frame 1938 does not 

Data frame 3925 does not have the column:'grownEnvironments.environments'.
Data frame 3926 does not have the column:'grownEnvironments.environments'.
Data frame 3927 does not have the column:'grownEnvironments.environments'.
Data frame 3928 does not have the column:'grownEnvironments.environments'.
Data frame 3929 does not have the column:'grownEnvironments.environments'.
Data frame 3930 does not have the column:'grownEnvironments.environments'.
Data frame 3931 does not have the column:'grownEnvironments.environments'.
Data frame 3932 does not have the column:'grownEnvironments.environments'.
Data frame 3933 does not have the column:'grownEnvironments.environments'.
Data frame 3934 does not have the column:'grownEnvironments.environments'.
Data frame 3935 does not have the column:'grownEnvironments.environments'.
Data frame 3936 does not have the column:'grownEnvironments.environments'.
Data frame 3937 does not have the column:'grownEnvironments.environments'.
Data frame 3938 does not 

experimentalEnvironments.environments
Data frame 26 does not have the column:'licence'.
Data frame 29 does not have the column:'licence'.
Data frame 30 does not have the column:'licence'.
Data frame 33 does not have the column:'licence'.
Data frame 37 does not have the column:'licence'.
Data frame 42 does not have the column:'licence'.
Data frame 51 does not have the column:'licence'.
Data frame 54 does not have the column:'licence'.
Data frame 64 does not have the column:'licence'.
Data frame 68 does not have the column:'licence'.
Data frame 71 does not have the column:'licence'.
Data frame 73 does not have the column:'licence'.
Data frame 80 does not have the column:'licence'.
Data frame 84 does not have the column:'licence'.
Data frame 108 does not have the column:'licence'.
Data frame 112 does not have the column:'licence'.
Data frame 114 does not have the column:'licence'.
Data frame 116 does not have the column:'licence'.
Data frame 118 does not have the column:'licence'.
Data fr

Data frame 1547 does not have the column:'licence'.
Data frame 1550 does not have the column:'licence'.
Data frame 1551 does not have the column:'licence'.
Data frame 1563 does not have the column:'licence'.
Data frame 1565 does not have the column:'licence'.
Data frame 1574 does not have the column:'licence'.
Data frame 1577 does not have the column:'licence'.
Data frame 1582 does not have the column:'licence'.
Data frame 1590 does not have the column:'licence'.
Data frame 1591 does not have the column:'licence'.
Data frame 1593 does not have the column:'licence'.
Data frame 1612 does not have the column:'licence'.
Data frame 1615 does not have the column:'licence'.
Data frame 1635 does not have the column:'licence'.
Data frame 1649 does not have the column:'licence'.
Data frame 1652 does not have the column:'licence'.
Data frame 1654 does not have the column:'licence'.
Data frame 1655 does not have the column:'licence'.
Data frame 1662 does not have the column:'licence'.
Data frame 1

...

Data frame 2137 does not have the column:'grownStages'.
Data frame 2138 does not have the column:'grownStages'.
Data frame 2139 does not have the column:'grownStages'.
Data frame 2140 does not have the column:'grownStages'.
Data frame 2141 does not have the column:'grownStages'.
Data frame 2142 does not have the column:'grownStages'.
Data frame 2143 does not have the column:'grownStages'.
Data frame 2144 does not have the column:'grownStages'.
Data frame 2145 does not have the column:'grownStages'.
Data frame 2146 does not have the column:'grownStages'.
Data frame 2147 does not have the column:'grownStages'.
Data frame 2148 does not have the column:'grownStages'.
Data frame 2149 does not have the column:'grownStages'.
Data frame 2150 does not have the column:'grownStages'.
Data frame 2151 does not have the column:'grownStages'.
Data frame 2152 does not have the column:'grownStages'.
Data frame 2153 does not have the column:'grownStages'.
Data frame 2154 does not have the column:'grownS

Data frame 4137 does not have the column:'grownStages'.
Data frame 4138 does not have the column:'grownStages'.
Data frame 4139 does not have the column:'grownStages'.
Data frame 4140 does not have the column:'grownStages'.
Data frame 4141 does not have the column:'grownStages'.
Data frame 4142 does not have the column:'grownStages'.
Data frame 4143 does not have the column:'grownStages'.
Data frame 4144 does not have the column:'grownStages'.
Data frame 4145 does not have the column:'grownStages'.
Data frame 4146 does not have the column:'grownStages'.
Data frame 4147 does not have the column:'grownStages'.
Data frame 4148 does not have the column:'grownStages'.
Data frame 4149 does not have the column:'grownStages'.
Data frame 4150 does not have the column:'grownStages'.
Data frame 4151 does not have the column:'grownStages'.
Data frame 4152 does not have the column:'grownStages'.
Data frame 4153 does not have the column:'grownStages'.
Data frame 4154 does not have the column:'grownS

Data frame 5729 does not have the column:'grownStages'.
Data frame 5730 does not have the column:'grownStages'.
Data frame 5731 does not have the column:'grownStages'.
Data frame 5732 does not have the column:'grownStages'.
Data frame 5733 does not have the column:'grownStages'.
Data frame 5734 does not have the column:'grownStages'.
Data frame 5735 does not have the column:'grownStages'.
Data frame 5736 does not have the column:'grownStages'.
Data frame 5737 does not have the column:'grownStages'.
Data frame 5738 does not have the column:'grownStages'.
Data frame 5739 does not have the column:'grownStages'.
Data frame 5740 does not have the column:'grownStages'.
Data frame 5741 does not have the column:'grownStages'.
Data frame 5742 does not have the column:'grownStages'.
Data frame 5743 does not have the column:'grownStages'.
Data frame 5744 does not have the column:'grownStages'.
Data frame 5745 does not have the column:'grownStages'.
Data frame 5746 does not have the column:'grownS

Data frame 2271 does not have the column:'ExternalIds'.
Data frame 2272 does not have the column:'ExternalIds'.
Data frame 2273 does not have the column:'ExternalIds'.
Data frame 2274 does not have the column:'ExternalIds'.
Data frame 2275 does not have the column:'ExternalIds'.
Data frame 2276 does not have the column:'ExternalIds'.
Data frame 2277 does not have the column:'ExternalIds'.
Data frame 2278 does not have the column:'ExternalIds'.
Data frame 2279 does not have the column:'ExternalIds'.
Data frame 2280 does not have the column:'ExternalIds'.
Data frame 2281 does not have the column:'ExternalIds'.
Data frame 2282 does not have the column:'ExternalIds'.
Data frame 2283 does not have the column:'ExternalIds'.
Data frame 2284 does not have the column:'ExternalIds'.
Data frame 2285 does not have the column:'ExternalIds'.
Data frame 2286 does not have the column:'ExternalIds'.
Data frame 2287 does not have the column:'ExternalIds'.
Data frame 2288 does not have the column:'Extern

Data frame 4770 does not have the column:'ExternalIds'.
Data frame 4771 does not have the column:'ExternalIds'.
Data frame 4772 does not have the column:'ExternalIds'.
Data frame 4773 does not have the column:'ExternalIds'.
Data frame 4774 does not have the column:'ExternalIds'.
Data frame 4775 does not have the column:'ExternalIds'.
Data frame 4776 does not have the column:'ExternalIds'.
Data frame 4777 does not have the column:'ExternalIds'.
Data frame 4778 does not have the column:'ExternalIds'.
Data frame 4779 does not have the column:'ExternalIds'.
Data frame 4780 does not have the column:'ExternalIds'.
Data frame 4781 does not have the column:'ExternalIds'.
Data frame 4782 does not have the column:'ExternalIds'.
Data frame 4783 does not have the column:'ExternalIds'.
Data frame 4784 does not have the column:'ExternalIds'.
Data frame 4785 does not have the column:'ExternalIds'.
Data frame 4786 does not have the column:'ExternalIds'.
Data frame 4787 does not have the column:'Extern

In [187]:
column_to_remove(dfs,"growthStages")

In [188]:
dfs[0].columns.values

array(['name', 'purpose', 'description', 'comments', 'id', 'login',
       'firstName', 'lastName', 'institution_name', 'logName',
       'executionDate', 'measurementDesc.technique',
       'measurementDesc.equipment', 'measurementDesc.description',
       'measurementDesc.parameters', 'hasAttachments', 'hasTSData',
       'hasPPAJobs', 'hasDataFiles', 'attachmentsSize', 'biodare1Id',
       'isOpenAccess', 'dataCategories', 'species', 'created', 'modified',
       'modifiedBy', 'dataCategory', 'id_experiment',
       'number_of_words_purpose', 'number_of_words_name',
       'number_of_words_description', 'number_of_words_comments'],
      dtype=object)